In [1]:
!pip install torch pandas tqdm transformers datasets trl peft bitsandbytes scikit-learn openpyxl


[notice] A new release of pip is available: 24.2 -> 25.0.1
[notice] To update, run: python -m pip install --upgrade pip


In [2]:
import numpy as np
import pandas as pd
import os
from tqdm import tqdm
import bitsandbytes as bnb
import torch
import torch.nn as nn
import transformers
from datasets import Dataset
from peft import LoraConfig, PeftConfig
from trl import SFTTrainer
from trl import setup_chat_format
from transformers import (AutoModelForCausalLM, 
                          AutoTokenizer, 
                          BitsAndBytesConfig, 
                          TrainingArguments, 
                          pipeline, 
                          logging)
from sklearn.metrics import (accuracy_score, 
                             classification_report, 
                             confusion_matrix)
from sklearn.model_selection import train_test_split

In [ ]:
Train_Path = "DFAR dataset/DFAR_trainset.csv"
Test_Path = "DFAR dataset/DFAR_testset.csv"

train_set = pd.read_csv(Train_Path, encoding='utf-8')
test_set = pd.read_csv(Test_Path, encoding='utf-8')

In [ ]:
train_set['Label'] = train_set['Label'].replace({0: "ethical", 1: "unethical"})
test_set['Label'] = test_set['Label'].replace({0: "ethical", 1: "unethical"})

In [ ]:
train_set = datasets.Dataset.from_dict(train_set)
test_set = datasets.Dataset.from_dict(test_set)

In [10]:
base_model_name = "microsoft/Phi-3.5-mini-instruct"

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=False,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype="float16",
)

model = AutoModelForCausalLM.from_pretrained(
    base_model_name,
    device_map="auto",
    torch_dtype="float16",
    quantization_config=bnb_config, 
)

model.config.use_cache = False
model.config.pretraining_tp = 1

tokenizer = AutoTokenizer.from_pretrained(base_model_name)

tokenizer.pad_token_id = tokenizer.eos_token_id

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
def finetune_label_prompts(example):
    output_texts = []
    for i in range(len(example['Statement'])):       
        text = f"### Question: Evaluate whether the statement is ethical or unethical without any reason. Statement: {example['Statement'][i]} The statement is \n ### Answer: {example['Label'][i]}"
        output_texts.append(text)
    return output_texts

In [ ]:
def predict(test, model, tokenizer):
    y_pred = []
    categories = ["ethical", "unethical"]
    
    for i in tqdm(range(len(test))):
        prompt = test.iloc[i]["Statement"]
        pipe = pipeline(task="text-generation", 
                        model=model, 
                        tokenizer=tokenizer, 
                        max_new_tokens=4, 
                        temperature=0.1)
        
        result = pipe(prompt)
        answer = result[0]['generated_text'].split("###label:")[-1].strip()
        
        # Determine the predicted category
        for category in categories:
            if category.lower() in answer.lower():
                y_pred.append(category)
                break
        else:
            y_pred.append("none")
    
    return y_pred

y_pred = predict(X_test, model, tokenizer)

  0%|          | 0/67 [00:00<?, ?it/s]Device set to use cuda:0
/usr/local/lib/python3.11/dist-packages/transformers/generation/configuration_utils.py:629: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
  1%|▏         | 1/67 [00:00<00:19,  3.33it/s]Device set to use cuda:0
Device set to use cuda:0
  4%|▍         | 3/67 [00:00<00:08,  7.57it/s]Device set to use cuda:0
Device set to use cuda:0
  7%|▋         | 5/67 [00:00<00:06,  9.88it/s]Device set to use cuda:0
Device set to use cuda:0
 10%|█         | 7/67 [00:00<00:05, 11.21it/s]Device set to use cuda:0
Device set to use cuda:0
 13%|█▎        | 9/67 [00:00<00:04, 12.13it/s]Device set to use cuda:0
Device set to use cuda:0
 16%|█▋        | 11/67 [00:01<00:04, 12.74it/s]Device set to use cuda:0
Device set to use cuda:0
 19%|█▉        | 13/67 [00:01<00:04, 13.08it/s]Devic

In [ ]:
def evaluate(y_true, y_pred):
    labels = ["ethical", "unethical"]
    mapping = {label: idx for idx, label in enumerate(labels)}
    
    def map_func(x):
        return mapping.get(x, -1)  # Map to -1 if not found, but should not occur with correct data
    
    y_true_mapped = np.vectorize(map_func)(y_true)
    y_pred_mapped = np.vectorize(map_func)(y_pred)
    
    # Calculate accuracy
    accuracy = accuracy_score(y_true=y_true_mapped, y_pred=y_pred_mapped)
    print(f'Accuracy: {accuracy:.3f}')
    
    # Generate accuracy report
    unique_labels = set(y_true_mapped)  # Get unique labels
    
    for label in unique_labels:
        label_indices = [i for i in range(len(y_true_mapped)) if y_true_mapped[i] == label]
        label_y_true = [y_true_mapped[i] for i in label_indices]
        label_y_pred = [y_pred_mapped[i] for i in label_indices]
        label_accuracy = accuracy_score(label_y_true, label_y_pred)
        print(f'Accuracy for label {labels[label]}: {label_accuracy:.3f}')
        
    # Generate classification report
    class_report = classification_report(y_true=y_true_mapped, y_pred=y_pred_mapped, target_names=labels, labels=list(range(len(labels))))
    print('\nClassification Report:')
    print(class_report)
    
    # Generate confusion matrix
    conf_matrix = confusion_matrix(y_true=y_true_mapped, y_pred=y_pred_mapped, labels=list(range(len(labels))))
    print('\nConfusion Matrix:')
    print(conf_matrix)


evaluate(y_true, y_pred)

Accuracy: 0.761
Accuracy for label Yes: 0.448
Accuracy for label No: 1.000

Classification Report:
              precision    recall  f1-score   support

         Yes       1.00      0.45      0.62        29
          No       0.70      1.00      0.83        38

    accuracy                           0.76        67
   macro avg       0.85      0.72      0.72        67
weighted avg       0.83      0.76      0.74        67


Confusion Matrix:
[[13 16]
 [ 0 38]]


In [14]:
def find_all_linear_names(model):
    cls = bnb.nn.Linear4bit
    lora_module_names = set()
    for name, module in model.named_modules():
        if isinstance(module, cls):
            names = name.split('.')
            lora_module_names.add(names[0] if len(names) == 1 else names[-1])
    if 'lm_head' in lora_module_names:  # needed for 16 bit
        lora_module_names.remove('lm_head')
    return list(lora_module_names)
modules = find_all_linear_names(model)
modules

['down_proj', 'o_proj', 'qkv_proj', 'gate_up_proj']

In [15]:
from transformers import TrainerCallback

class CustomEvalCallback(TrainerCallback):
    def on_evaluate(self, args, state, control, model, **kwargs):
        print("\nEvaluating model...\n")
        
        # Generate predictions on X_test
        y_pred = predict(X_test, model, tokenizer)
        
        # Evaluate predictions
        evaluate(y_true, y_pred)

In [16]:
from trl import SFTTrainer, SFTConfig
from transformers import TrainingArguments, DataCollatorForSeq2Seq

output_dir="Phi-3.5-mini-instruct"

peft_config = LoraConfig(
    lora_alpha=16,
    lora_dropout=0,
    r=64,
    bias="none",
    task_type="CAUSAL_LM",
    target_modules=modules,
)

training_arguments = SFTConfig(
    output_dir=output_dir,                    # directory to save and repository id
    num_train_epochs=30,                       # number of training epochs
    per_device_train_batch_size=1,            # batch size per device during training
    gradient_accumulation_steps=4,            # number of steps before performing a backward/update pass
    gradient_checkpointing=True,              # use gradient checkpointing to save memory
    optim="paged_adamw_8bit",
    logging_steps=1,                         
    learning_rate=2e-5,                       # learning rate, based on QLoRA paper
    weight_decay=0.001,
    fp16 = False,
    bf16 = False,
    max_grad_norm=0.3,                        # max gradient norm based on QLoRA paper
    max_steps=-1,
    warmup_ratio=0.03,                        # warmup ratio based on QLoRA paper
    group_by_length=False,
    lr_scheduler_type="cosine",               # use cosine learning rate scheduler
    # report_to="wandb",                  # report metrics to w&b
    eval_strategy="epoch",              # save checkpoint every epoch
    eval_steps = 0.2
)



In [18]:
trainer = SFTTrainer(
    model=model,
    args=training_arguments,
    train_dataset=train_data,
    eval_dataset=eval_data,
    tokenizer=tokenizer,
    peft_config=peft_config,
    #dataset_text_field="Sentiment",
    formatting_func=formatting_prompts_func,
    callbacks=[CustomEvalCallback()] 


)

/tmp/ipykernel_1776/2653832121.py:1: FutureWarning: `tokenizer` is deprecated and removed starting from version 0.16.0 for `SFTTrainer.__init__`. Use `processing_class` instead.
  trainer = SFTTrainer(


Applying formatting function to train dataset:   0%|          | 0/526 [00:00<?, ? examples/s]

Converting train dataset to ChatML:   0%|          | 0/526 [00:00<?, ? examples/s]

Applying chat template to train dataset:   0%|          | 0/526 [00:00<?, ? examples/s]

Tokenizing train dataset:   0%|          | 0/526 [00:00<?, ? examples/s]

...

Converting eval dataset to ChatML:   0%|          | 0/65 [00:00<?, ? examples/s]

Applying chat template to eval dataset:   0%|          | 0/65 [00:00<?, ? examples/s]

Tokenizing eval dataset:   0%|          | 0/65 [00:00<?, ? examples/s]

Tokenizing eval dataset:   0%|          | 0/65 [00:00<?, ? examples/s]

No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [19]:
trainer.train()

/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:295: FutureWarning: `torch.cpu.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cpu', args...)` instead.
  with torch.enable_grad(), device_autocast_ctx, torch.cpu.amp.autocast(**ctx.cpu_autocast_kwargs):  # type: ignore[attr-defined]



Evaluating model...



  0%|          | 0/67 [00:00<?, ?it/s]Device set to use cuda:0
The model 'PeftModelForCausalLM' is not supported for text-generation. Supported models are ['AriaTextForCausalLM', 'BambaForCausalLM', 'BartForCausalLM', 'BertLMHeadModel', 'BertGenerationDecoder', 'BigBirdForCausalLM', 'BigBirdPegasusForCausalLM', 'BioGptForCausalLM', 'BlenderbotForCausalLM', 'BlenderbotSmallForCausalLM', 'BloomForCausalLM', 'CamembertForCausalLM', 'LlamaForCausalLM', 'CodeGenForCausalLM', 'CohereForCausalLM', 'Cohere2ForCausalLM', 'CpmAntForCausalLM', 'CTRLLMHeadModel', 'Data2VecTextForCausalLM', 'DbrxForCausalLM', 'DiffLlamaForCausalLM', 'ElectraForCausalLM', 'Emu3ForCausalLM', 'ErnieForCausalLM', 'FalconForCausalLM', 'FalconMambaForCausalLM', 'FuyuForCausalLM', 'GemmaForCausalLM', 'Gemma2ForCausalLM', 'GitForCausalLM', 'GlmForCausalLM', 'GotOcr2ForConditionalGeneration', 'GPT2LMHeadModel', 'GPT2LMHeadModel', 'GPTBigCodeForCausalLM', 'GPTNeoForCausalLM', 'GPTNeoXForCausalLM', 'GPTNeoXJapaneseForCausalLM

Accuracy: 0.746
Accuracy for label Yes: 0.621
Accuracy for label No: 0.842

Classification Report:
              precision    recall  f1-score   support

         Yes       0.75      0.62      0.68        29
          No       0.74      0.84      0.79        38

    accuracy                           0.75        67
   macro avg       0.75      0.73      0.73        67
weighted avg       0.75      0.75      0.74        67


Confusion Matrix:
[[18 11]
 [ 6 32]]



/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:295: FutureWarning: `torch.cpu.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cpu', args...)` instead.
  with torch.enable_grad(), device_autocast_ctx, torch.cpu.amp.autocast(**ctx.cpu_autocast_kwargs):  # type: ignore[attr-defined]


...


/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:295: FutureWarning: `torch.cpu.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cpu', args...)` instead.
  with torch.enable_grad(), device_autocast_ctx, torch.cpu.amp.autocast(**ctx.cpu_autocast_kwargs):  # type: ignore[attr-defined]



Evaluating model...



  0%|          | 0/67 [00:00<?, ?it/s]Device set to use cuda:0
The model 'PeftModelForCausalLM' is not supported for text-generation. Supported models are ['AriaTextForCausalLM', 'BambaForCausalLM', 'BartForCausalLM', 'BertLMHeadModel', 'BertGenerationDecoder', 'BigBirdForCausalLM', 'BigBirdPegasusForCausalLM', 'BioGptForCausalLM', 'BlenderbotForCausalLM', 'BlenderbotSmallForCausalLM', 'BloomForCausalLM', 'CamembertForCausalLM', 'LlamaForCausalLM', 'CodeGenForCausalLM', 'CohereForCausalLM', 'Cohere2ForCausalLM', 'CpmAntForCausalLM', 'CTRLLMHeadModel', 'Data2VecTextForCausalLM', 'DbrxForCausalLM', 'DiffLlamaForCausalLM', 'ElectraForCausalLM', 'Emu3ForCausalLM', 'ErnieForCausalLM', 'FalconForCausalLM', 'FalconMambaForCausalLM', 'FuyuForCausalLM', 'GemmaForCausalLM', 'Gemma2ForCausalLM', 'GitForCausalLM', 'GlmForCausalLM', 'GotOcr2ForConditionalGeneration', 'GPT2LMHeadModel', 'GPT2LMHeadModel', 'GPTBigCodeForCausalLM', 'GPTNeoForCausalLM', 'GPTNeoXForCausalLM', 'GPTNeoXJapaneseForCausalLM

Accuracy: 0.940
Accuracy for label Yes: 0.931
Accuracy for label No: 0.947

Classification Report:
              precision    recall  f1-score   support

         Yes       0.93      0.93      0.93        29
          No       0.95      0.95      0.95        38

    accuracy                           0.94        67
   macro avg       0.94      0.94      0.94        67
weighted avg       0.94      0.94      0.94        67


Confusion Matrix:
[[27  2]
 [ 2 36]]


TrainOutput(global_step=3930, training_loss=0.09157839940040924, metrics={'train_runtime': 3374.3216, 'train_samples_per_second': 4.676, 'train_steps_per_second': 1.165, 'total_flos': 1.4624133256479744e+17, 'train_loss': 0.09157839940040924})

In [ ]:
y_pred = predict(X_test, model, tokenizer)
evaluate(y_true, y_pred)

In [ ]:
from peft import LoraConfig
from peft import PeftModel, PeftConfig
from peft import prepare_model_for_kbit_training
# Loading LORA weights

model.config.use_cache = False
PATH = "./Phi-3.5-mini-instruct/checkpoint-500"
base_model = PeftModel.from_pretrained(model, PATH)
base_model = base_model.merge_and_unload()

In [ ]:
y_pred = predict(X_test, base_model, tokenizer)
evaluate(y_true, y_pred)